# Redshift ML for Game Analytics

This notebooks helps you to demo how Redshift ML can be used in gaming industry for player retention and also for providing next best package for player retention.

## Pre-requisties

1. Create Amazon Redshift cluster - https://docs.aws.amazon.com/redshift/latest/gsg/rs-gsg-launch-sample-cluster.html
    
    Note: You can also demo this on Redshift Serverless
2. Ensure you setup an IAM role as default IAM role.  Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/default-iam-role.html#managing-iam-role-console) for instructions.

**Ingest Game Data**    

        
In this task,   
    -   you will create tables to store game data   
    -   load data from S3 to Redshift.

In [0]:
drop table if exists game_attempts;
drop table if exists  users_to_predict;
drop table if exists training_users;
drop table if exists  validation_users;

create table game_attempts
    (user_id numeric(10, 0), -- User ID.  This is the key to match with other datasets.
    level_id numeric(5, 0), -- Game level ID
    f_success integer, -- Indicates whether user completed the level (1: completed, 0: fails).
    f_duration real, -- duration of the attempt.  Units in seconds
    f_reststep real, -- The ratio of the remaining steps to the limited steps.  Failure is 0.
    f_help integer, -- Whether extra help, such as props and hints, was used.  1- used, 0- not used
    game_time timestamp, -- Attempt timestamp
    bp_used boolean -- Whether bonus packages used or not.  true: used, false: not used.
    );


    create table training_users
    (user_id numeric(10, 0), -- User ID
    lost_label boolean, -- Indicated if user retained or lost.  true: lost ,  false: retained
    bp_category integer -- bonus package category codes
    );

    create table validation_users 
    (user_id numeric(10, 0), -- User ID
    lost_label boolean, -- Indicated if user retained or lost.  true: lost , false: retained
    bp_category integer -- bonus package category codes
    );

    create table users_to_predict 
    (user_id numeric(10, 0) -- User ID
    );

COPY game_attempts
FROM 's3://redshift-demos/data/gamejam/game_attempts.csv' 
IAM_ROLE default
FORMAT AS CSV
IGNOREHEADER 1 
REGION AS 'us-east-1';

COPY validation_users
FROM 's3://redshift-demos/data/gamejam/validation_users.csv' 
IAM_ROLE default
FORMAT AS CSV
IGNOREHEADER 1 
REGION AS 'us-east-1';


COPY training_users
FROM 's3://redshift-demos/data/gamejam/training_users.csv' 
IAM_ROLE default
FORMAT AS CSV
IGNOREHEADER 1 
REGION AS 'us-east-1';

COPY users_to_predict
FROM 's3://redshift-demos/data/gamejam/users_to_predict.csv' 
IAM_ROLE default
FORMAT AS CSV
IGNOREHEADER 1 
REGION AS 'us-east-1';

**Feature Engineering**     


In this task, you will prepare the data to feed into the model.  It includes creating derived variables, type casting and handling missing values etc.,

In [0]:
create table players_training_data as    
select t.user_id, 
    count(level_id) no_of_levels_played, 
    max(level_id) max_level_played, 
    sum(f_success) success_attempts, 
    count(*) - sum(f_success) failed_attempts,
    sum(f_help) times_used_help, 
    count(*) - sum(f_help) times_not_used_help,
    sum(f_duration) total_play_duration,
    avg(f_reststep) ratio_to_finish,
    max(g.bp_used::int)::boolean bp_used,
    t.bp_category,    
    t.lost_label    
from game_attempts g, training_users t    
where g.user_id=t.user_id    
group by t.user_id, t.lost_label,t.bp_category;


create table players_validation_data as    
select v.user_id, 
    count(level_id) no_of_levels_played, 
    max(level_id) max_level_played, 
    sum(f_success) success_attempts, 
    count(*) - sum(f_success) failed_attempts,
    sum(f_help) times_used_help, 
    count(*) - sum(f_help) times_not_used_help,
    sum(f_duration) total_play_duration,
    avg(f_reststep) ratio_to_finish,
    max(g.bp_used::int)::boolean bp_used,
    v.bp_category,    
    v.lost_label    
from game_attempts g, validation_users v    
where g.user_id=v.user_id    
group by v.user_id, v.lost_label, v.bp_category;

create table players_test_data as    
select t.user_id, count(level_id) no_of_levels_played, max(level_id) max_level_played,
   sum(f_success) success_attempts, count(*) - sum(f_success) failed_attempts,
    sum(f_help) times_used_help, count(*) - sum(f_help) times_not_used_help,
    sum(f_duration) total_play_duration,
    avg(f_reststep) ratio_to_finish,
    max(g.bp_used::int)::boolean bp_used    
from game_attempts g, users_to_predict t
where g.user_id=t.user_id    
group by t.user_id;

**Create model for predicting player retention**    

References on how to create ML model in Redshift using SQLs:    
https://docs.aws.amazon.com/redshift/latest/dg/r_CREATE_MODEL.html  
https://www.youtube.com/watch?v=pJF2kYGtO4A

In [0]:
CREATE MODEL mod_predict_player_retention    
FROM (    
    SELECT        
    user_id ,    
    no_of_levels_played ,    
    max_level_played ,    
    success_attempts ,    
    bp_used,    
    failed_attempts,    
    times_used_help ,    
    times_not_used_help,    
    total_play_duration,    
    ratio_to_finish,      
    lost_label     
 FROM    
     players_training_data )    
     TARGET lost_label    
 FUNCTION fun_predict_player_retention   
 IAM_ROLE default
 SETTINGS (    
   S3_BUCKET '<your-s3-bucket-name>'    
  )    ;

**Review model status**

In [0]:
show model mod_predict_player_retention;

**Create another model to predict bonus packages**

In [0]:
CREATE MODEL mod_predict_bp_category
FROM (    
select    
    user_id,    
    no_of_levels_played ,    
    max_level_played ,    
    success_attempts ,    
    failed_attempts ,    
    times_used_help ,    
    total_play_duration ,    
    bp_used,    
    bp_category        
FROM    
  players_training_data)    
TARGET bp_category    
FUNCTION fun_predict_bp_category      
IAM_ROLE default    
SETTINGS (    
  S3_BUCKET '<your-s3-bucket-name>'     
  );

**Review model status**

In [0]:
show model mod_predict_bp_category;

**Check accuracy of both the models**    

Run below queriesy to find accuracy of models.    
These SQLs compares actual values with predicted value by the model.

In [0]:
WITH validation_data    
 AS (    
      SELECT lost_label as actual,     
    fun_predict_player_retention(user_id, no_of_levels_played,max_level_played,success_attempts,bp_used,failed_attempts,times_used_help,times_not_used_help,total_play_duration,ratio_to_finish) AS predicted,    
    CASE WHEN actual = predicted THEN 1::INT    
         ELSE 0::INT END AS correct    
    FROM players_validation_data    
    ),
 aggr_data AS (
     SELECT SUM(correct) as num_correct, COUNT(*) as total FROM validation_data
 )
 SELECT round((num_correct::float/total::float),3) AS accuracy FROM aggr_data;


 WITH validation_data    
 AS (    
      SELECT  bp_category as actual,     
    fun_predict_bp_category(user_id, no_of_levels_played , max_level_played ,success_attempts , failed_attempts , times_used_help , total_play_duration ,
    bp_used) AS predicted,    
    CASE WHEN actual = predicted THEN 1::INT    
         ELSE 0::INT END AS correct    
    FROM players_validation_data    
    ),
 aggr_data AS (
     SELECT SUM(correct) as num_correct, COUNT(*) as total FROM validation_data
 )
 SELECT round((num_correct::float/total::float),3) AS accuracy FROM aggr_data;

**Queries to predict

- User retention
- What pacakages to recommend for player predicted to max_level_played

In [0]:
--Query to predict user retention 

SELECT    
user_id,  fun_predict_player_retention(user_id, no_of_levels_played,max_level_played,success_attempts,bp_used,failed_attempts,times_used_help,times_not_used_help,total_play_duration,ratio_to_finish) as predicted_lost_label    
FROM players_test_data;



--Query to predict bonus package for users, who are predicted to leave
WITH possible_lost_users    
AS (    
    SELECT
        user_id, fun_predict_player_retention(user_id, no_of_levels_played,max_level_played,success_attempts,bp_used,failed_attempts,times_used_help,times_not_used_help,total_play_duration,ratio_to_finish) as predicted_lost_label
    FROM players_test_data    
      where 
      predicted_lost_label = false    
    )    
SELECT user_id, fun_predict_bp_category(user_id,
    no_of_levels_played ,
    max_level_played ,
    success_attempts ,
    failed_attempts ,
    times_used_help ,
    total_play_duration ,
    bp_used) as predicted_bonus_package_class    
FROM players_test_data    
WHERE user_id in 
(    select user_id from possible_lost_users
);

In [0]:
-- Query to find user count by categories

WITH possible_lost_users    
AS (    
    SELECT
        user_id, fun_predict_player_retention(user_id, no_of_levels_played,max_level_played,success_attempts,bp_used,failed_attempts,times_used_help,times_not_used_help,total_play_duration,ratio_to_finish) as predicted_lost_label
    FROM players_test_data    
      where 
      predicted_lost_label = false    
    )    
SELECT fun_predict_bp_category(user_id,
    no_of_levels_played ,
    max_level_played ,
    success_attempts ,
    failed_attempts ,
    times_used_help ,
    total_play_duration ,
    bp_used) as predicted_bonus_package_class, count(user_id)
FROM players_test_data    
WHERE user_id in 
(    select user_id from possible_lost_users
)
group by 1

## Cleanup 

Delete Redshift cluster created for the demo. https://docs.aws.amazon.com/redshift/latest/mgmt/managing-clusters-console.html#delete-cluster